In [26]:
import nltk
from nltk.tokenize.texttiling import TextTilingTokenizer
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [27]:
from nltk.tokenize.texttiling import smooth

In [28]:
import math
import re

try:
    import numpy
except ImportError:
    pass

from nltk.tokenize.api import TokenizerI

BLOCK_COMPARISON, VOCABULARY_INTRODUCTION = 0, 1
LC, HC = 0, 1
DEFAULT_SMOOTHING = [0]

In [44]:
class TextTilingTokenizer(TokenizerI):
    def __init__(
        self,
        w = 5000,
        k=10,
        similarity_method=BLOCK_COMPARISON,
        stopwords=None,
        smoothing_method=DEFAULT_SMOOTHING,
        smoothing_width=2,
        smoothing_rounds=1,
        cutoff_policy=HC,
        demo_mode=False,
    ):

        if stopwords is None:
            from nltk.corpus import stopwords

            stopwords = stopwords.words("english")
        self.__dict__.update(locals())
        del self.__dict__["self"]

    def tokenize(self, text):
        """Return a tokenized copy of *text*, where each "token" represents
        a separate topic."""

        lowercase_text = text.lower()
        paragraph_breaks = self._mark_paragraph_breaks(text)
        text_length = len(lowercase_text)

        # Tokenization step starts here

        # Remove punctuation
        nopunct_text = "".join(
            c for c in lowercase_text if re.match(r"[a-z\-' \n\t]", c)
        )
        nopunct_par_breaks = self._mark_paragraph_breaks(nopunct_text)

        tokseqs = self._divide_to_tokensequences(nopunct_text)

        # The morphological stemming step mentioned in the TextTile
        # paper is not implemented.  A comment in the original C
        # implementation states that it offers no benefit to the
        # process. It might be interesting to test the existing
        # stemmers though.
        # words = _stem_words(words)

        # Filter stopwords
        for ts in tokseqs:
            ts.wrdindex_list = [
                wi for wi in ts.wrdindex_list if wi[0] not in self.stopwords
            ]

        token_table = self._create_token_table(tokseqs, nopunct_par_breaks)
        # End of the Tokenization step

        # Lexical score determination
        if self.similarity_method == BLOCK_COMPARISON:
            gap_scores = self._block_comparison(tokseqs, token_table)
        elif self.similarity_method == VOCABULARY_INTRODUCTION:
            raise NotImplementedError("Vocabulary introduction not implemented")
        else:
            raise ValueError(
                f"Similarity method {self.similarity_method} not recognized"
            )

        if self.smoothing_method == DEFAULT_SMOOTHING:
            smooth_scores = self._smooth_scores(gap_scores)
        else:
            raise ValueError(f"Smoothing method {self.smoothing_method} not recognized")
        # End of Lexical score Determination

        # Boundary identification
        depth_scores = self._depth_scores(smooth_scores)
        segment_boundaries = self._identify_boundaries(depth_scores)

        normalized_boundaries = self._normalize_boundaries(
            text, segment_boundaries, paragraph_breaks
        )
        # End of Boundary Identification
        segmented_text = []
        prevb = 0

        for b in normalized_boundaries:
            if b == 0:
                continue
            segmented_text.append(text[prevb:b])
            prevb = b

        if prevb < text_length:  # append any text that may be remaining
            segmented_text.append(text[prevb:])

        if not segmented_text:
            segmented_text = [text]

        if self.demo_mode:
            return gap_scores, smooth_scores, depth_scores, segment_boundaries
        return segmented_text


    def _block_comparison(self, tokseqs, token_table):
        """Implements the block comparison method"""

        def blk_frq(tok, block):
            ts_occs = filter(lambda o: o[0] in block, token_table[tok].ts_occurences)
            freq = sum(tsocc[1] for tsocc in ts_occs)
            return freq

        gap_scores = []
        numgaps = len(tokseqs) - 1

        for curr_gap in range(numgaps):
            score_dividend, score_divisor_b1, score_divisor_b2 = 0.0, 0.0, 0.0
            score = 0.0
            # adjust window size for boundary conditions
            if curr_gap < self.k - 1:
                window_size = curr_gap + 1
            elif curr_gap > numgaps - self.k:
                window_size = numgaps - curr_gap
            else:
                window_size = self.k

            b1 = [ts.index for ts in tokseqs[curr_gap - window_size + 1 : curr_gap + 1]]
            b2 = [ts.index for ts in tokseqs[curr_gap + 1 : curr_gap + window_size + 1]]

            for t in token_table:
                score_dividend += blk_frq(t, b1) * blk_frq(t, b2)
                score_divisor_b1 += blk_frq(t, b1) ** 2
                score_divisor_b2 += blk_frq(t, b2) ** 2
            try:
                score = score_dividend / math.sqrt(score_divisor_b1 * score_divisor_b2)
            except ZeroDivisionError:
                pass  # score += 0.0

            gap_scores.append(score)

        return gap_scores

    def _smooth_scores(self, gap_scores):
        "Wraps the smooth function from the SciPy Cookbook"
        return list(
            smooth(numpy.array(gap_scores[:]), window_len=self.smoothing_width + 1)
        )

    def _mark_paragraph_breaks(self, text):
        """Identifies indented text or line breaks as the beginning of
        paragraphs"""
        MIN_PARAGRAPH = 100
        pattern = re.compile("[ \t\r\f\v]*\n[ \t\r\f\v]*\n[ \t\r\f\v]*")
        matches = pattern.finditer(text)

        last_break = 0
        pbreaks = [0]
        for pb in matches:
            if pb.start() - last_break < MIN_PARAGRAPH:
                continue
            else:
                pbreaks.append(pb.start())
                last_break = pb.start()

        return pbreaks

    def _divide_to_tokensequences(self, text):
        "Divides the text into pseudosentences of fixed size"
        w = self.w
        wrdindex_list = []
        matches = re.finditer(r"\w+", text)
        for match in matches:
            wrdindex_list.append((match.group(), match.start()))
        return [
            TokenSequence(i / w, wrdindex_list[i : i + w])
            for i in range(0, len(wrdindex_list), w)
        ]

    def _create_token_table(self, token_sequences, par_breaks):
        "Creates a table of TokenTableFields"
        token_table = {}
        current_par = 0
        current_tok_seq = 0
        pb_iter = par_breaks.__iter__()
        current_par_break = next(pb_iter)
        if current_par_break == 0:
            try:
                current_par_break = next(pb_iter)  # skip break at 0
            except StopIteration as e:
                raise ValueError(
                    "No paragraph breaks were found(text too short perhaps?)"
                ) from e
        for ts in token_sequences:
            for word, index in ts.wrdindex_list:
                try:
                    while index > current_par_break:
                        current_par_break = next(pb_iter)
                        current_par += 1
                except StopIteration:
                    # hit bottom
                    pass

                if word in token_table:
                    token_table[word].total_count += 1

                    if token_table[word].last_par != current_par:
                        token_table[word].last_par = current_par
                        token_table[word].par_count += 1

                    if token_table[word].last_tok_seq != current_tok_seq:
                        token_table[word].last_tok_seq = current_tok_seq
                        token_table[word].ts_occurences.append([current_tok_seq, 1])
                    else:
                        token_table[word].ts_occurences[-1][1] += 1
                else:  # new word
                    token_table[word] = TokenTableField(
                        first_pos=index,
                        ts_occurences=[[current_tok_seq, 1]],
                        total_count=1,
                        par_count=1,
                        last_par=current_par,
                        last_tok_seq=current_tok_seq,
                    )

            current_tok_seq += 1

        return token_table

    def _identify_boundaries(self, depth_scores):
        """Identifies boundaries at the peaks of similarity score
        differences"""

        boundaries = [0 for x in depth_scores]

        avg = sum(depth_scores) / len(depth_scores)
        stdev = numpy.std(depth_scores)

        if self.cutoff_policy == LC:
            cutoff = avg - stdev
        else:
            cutoff = avg - stdev / 2.0

        depth_tuples = sorted(zip(depth_scores, range(len(depth_scores))))
        depth_tuples.reverse()
        hp = list(filter(lambda x: x[0] > cutoff, depth_tuples))

        for dt in hp:
            boundaries[dt[1]] = 1
            for dt2 in hp:  # undo if there is a boundary close already
                if (
                    dt[1] != dt2[1]
                    and abs(dt2[1] - dt[1]) < 4
                    and boundaries[dt2[1]] == 1
                ):
                    boundaries[dt[1]] = 0
        return boundaries

    def _depth_scores(self, scores):
        """Calculates the depth of each gap, i.e. the average difference
        between the left and right peaks and the gap's score"""

        depth_scores = [0 for x in scores]
        # clip boundaries: this holds on the rule of thumb(my thumb)
        # that a section shouldn't be smaller than at least 2
        # pseudosentences for small texts and around 5 for larger ones.

        clip = min(max(len(scores) // 10, 2), 5)
        index = clip

        for gapscore in scores[clip:-clip]:
            lpeak = gapscore
            for score in scores[index::-1]:
                if score >= lpeak:
                    lpeak = score
                else:
                    break
            rpeak = gapscore
            for score in scores[index:]:
                if score >= rpeak:
                    rpeak = score
                else:
                    break
            depth_scores[index] = lpeak + rpeak - 2 * gapscore
            index += 1

        return depth_scores

    def _normalize_boundaries(self, text, boundaries, paragraph_breaks):
        """Normalize the boundaries identified to the original text's
        paragraph breaks"""

        norm_boundaries = []
        char_count, word_count, gaps_seen = 0, 0, 0
        seen_word = False

        for char in text:
            char_count += 1
            if char in " \t\n" and seen_word:
                seen_word = False
                word_count += 1
            if char not in " \t\n" and not seen_word:
                seen_word = True
            if gaps_seen < len(boundaries) and word_count > (
                max(gaps_seen * self.w, self.w)
            ):
                if boundaries[gaps_seen] == 1:
                    # find closest paragraph break
                    best_fit = len(text)
                    for br in paragraph_breaks:
                        if best_fit > abs(br - char_count):
                            best_fit = abs(br - char_count)
                            bestbr = br
                        else:
                            break
                    if bestbr not in norm_boundaries:  # avoid duplicates
                        norm_boundaries.append(bestbr)
                gaps_seen += 1

        return norm_boundaries

In [30]:
class TokenTableField:
    """A field in the token table holding parameters for each token,
    used later in the process"""

    def __init__(
        self,
        first_pos,
        ts_occurences,
        total_count=1,
        par_count=1,
        last_par=0,
        last_tok_seq=None,
    ):
        self.__dict__.update(locals())
        del self.__dict__["self"]


In [31]:
class TokenSequence:
    "A token list with its original length and its index"

    def __init__(self, index, wrdindex_list, original_length=None):
        original_length = original_length or len(wrdindex_list)
        self.__dict__.update(locals())
        del self.__dict__["self"]



# Pasted from the SciPy cookbook: https://www.scipy.org/Cookbook/SignalSmooth
    def smooth(x, window_len=11, window="flat"):
      """smooth the data using a window with requested size.

      This method is based on the convolution of a scaled window with the signal.
      The signal is prepared by introducing reflected copies of the signal
      (with the window size) in both ends so that transient parts are minimized
      in the beginning and end part of the output signal.

      :param x: the input signal
      :param window_len: the dimension of the smoothing window; should be an odd integer
      :param window: the type of window from 'flat', 'hanning', 'hamming', 'bartlett', 'blackman'
          flat window will produce a moving average smoothing.

      :return: the smoothed signal

      example::

          t=linspace(-2,2,0.1)
          x=sin(t)+randn(len(t))*0.1
          y=smooth(x)

      :see also: numpy.hanning, numpy.hamming, numpy.bartlett, numpy.blackman, numpy.convolve,
          scipy.signal.lfilter

      TODO: the window parameter could be the window itself if an array instead of a string
      """

      if x.ndim != 1:
          raise ValueError("smooth only accepts 1 dimension arrays.")

      if x.size < window_len:
          raise ValueError("Input vector needs to be bigger than window size.")

      if window_len < 3:
          return x

      if window not in ["flat", "hanning", "hamming", "bartlett", "blackman"]:
          raise ValueError(
              "Window is on of 'flat', 'hanning', 'hamming', 'bartlett', 'blackman'"
          )

      s = numpy.r_[2 * x[0] - x[window_len:1:-1], x, 2 * x[-1] - x[-1:-window_len:-1]]

      # print(len(s))
      if window == "flat":  # moving average
          w = numpy.ones(window_len, "d")
      else:
          w = eval("numpy." + window + "(window_len)")

      y = numpy.convolve(w / w.sum(), s, mode="same")

      return y[window_len - 1 : -window_len + 1]



    def demo(text=None):
      from matplotlib import pylab

      from nltk.corpus import brown

      tt = TextTilingTokenizer(demo_mode=True)
      if text is None:
          text = brown.raw()[:10000]
      s, ss, d, b = tt.tokenize(text)
      pylab.xlabel("Sentence Gap index")
      pylab.ylabel("Gap Scores")
      pylab.plot(range(len(s)), s, label="Gap Scores")
      pylab.plot(range(len(ss)), ss, label="Smoothed Gap scores")
      pylab.plot(range(len(d)), d, label="Depth scores")
      pylab.stem(range(len(b)), b)
      pylab.legend()
      pylab.show()


In [32]:
with open('/content/drive/MyDrive/math_data.txt', 'r') as file:
    text = file.read()

In [34]:
tokenizer = TextTilingTokenizer()

In [35]:
segmented_text = tokenizer.tokenize(text)

In [36]:
segmented_text

['text\tlabel\t\t\t\t\t\t\t\t\t\t\n"The following content is\nprovided under a Creative Commons license. Your support will help\nMIT OpenCourseWare continue to offer high quality\neducational resources for free. To make a donation, or to\nview additional materials from hundreds of MIT courses,\nvisit MIT OpenCourseWare at ocw.mit.edu. PROFESSOR: So,\nProfessor Jerison is relaxing in sunny\nLondon, Ontario today and sent me in as\nhis substitute again. I\'m glad to the here\nand see you all again. So our agenda today: he\nsaid that he\'d already talked about power series\nand Taylor\'s formula, I guess on last week\nright, on Friday? So I\'m going to go a\nlittle further with that and show you some examples,\nshow you some applications, and then I have this\ncourse evaluation survey that I\'ll hand out in the last\n10 minutes or so of the class. I also have this handout\nthat he made that says 18.01 end of term 2007. If you didn\'t pick this up\ncoming in, grab it going out. People tend

In [45]:
tokenizer = TextTilingTokenizer(demo_mode=True)

In [46]:
gap_scores, smooth_scores, depth_scores, segment_boundaries = tokenizer.tokenize(text)

In [47]:
gap_scores

[0.2777898280750838,
 0.4740637028201632,
 0.5767579420749747,
 0.7346831312870301,
 0.6849338733742966,
 0.6689761034623637,
 0.7342259592885017,
 0.7826040394544781,
 0.8093851678498029,
 0.8081652030882076,
 0.8152909702847699,
 0.8202808803130003,
 0.8234148833887746,
 0.8366723605926454,
 0.8282534395358141,
 0.8249495702569383,
 0.8304539355655951,
 0.8276448288084267,
 0.8374059924059718,
 0.7994043315198751,
 0.781707775103461,
 0.7631948168590403,
 0.787883692094383,
 0.7713994927452934,
 0.7530874958225567,
 0.7888357201058864,
 0.8116330486223436,
 0.8073354463175481,
 0.8172309455224304,
 0.8332973237630428,
 0.8492425556737825,
 0.8503469207621228,
 0.8025881956626391,
 0.8245098961213343,
 0.8285510345183494,
 0.8513095329108612,
 0.8444969284503516,
 0.8203289678527642,
 0.8084135669703477,
 0.8183795329859286,
 0.8266033937672352,
 0.8118609094896546,
 0.8160159047736075,
 0.8267969137310507,
 0.7926632431241462,
 0.8135332625693342,
 0.8313013166177327,
 0.845266147966

In [48]:
smooth_scores

[0.2435584149901466,
 0.44287049099007386,
 0.5951682587273892,
 0.665458315578767,
 0.6961977027078967,
 0.6960453120417206,
 0.7286020340684478,
 0.7754050555309274,
 0.8000514701308294,
 0.8109471137409268,
 0.8145790178953259,
 0.8196622446621815,
 0.8267893747648066,
 0.8294468945057445,
 0.8299584567951326,
 0.8278856484527823,
 0.82768277821032,
 0.8318349189266645,
 0.8214850509114245,
 0.8061726996764359,
 0.7814356411607921,
 0.7775954280189613,
 0.7741593338995723,
 0.770790226887411,
 0.7711075695579122,
 0.7845187548502622,
 0.8026014050152595,
 0.8120664801541073,
 0.819287905201007,
 0.8332569416530853,
 0.844295600066316,
 0.834059224032848,
 0.825815004182032,
 0.8185497087674408,
 0.8347901545168482,
 0.8414524986265207,
 0.8387118097379923,
 0.8244131544244878,
 0.8157073559363468,
 0.8177988312411705,
 0.8189479454142727,
 0.818160069343499,
 0.8182245759981042,
 0.8118253538762681,
 0.8109978064748437,
 0.8124992741037376,
 0.8300335757177459,
 0.834173824935837,
 

In [49]:
depth_scores

[0,
 0,
 0,
 0,
 0,
 0.1340655354195881,
 0.10135642272668477,
 0.05455340126420505,
 0.029906986664303137,
 0.01901134305420582,
 0.015379438899806752,
 0.010296212132951066,
 0.0031690820303260647,
 0.00051156228938809,
 0.0,
 0.002072808342350241,
 0.0064278193011571005,
 0.0,
 0.010349868015240071,
 0.02566221925022849,
 0.050399277765872386,
 0.05423949090770308,
 0.05767558502709225,
 0.1345500652181586,
 0.07318803050840383,
 0.05977684521605364,
 0.04169419505105654,
 0.03222911991220867,
 0.02500769486530907,
 0.011038658413230706,
 0.0,
 0.010236376033468053,
 0.018480595884283968,
 0.048648681157955176,
 0.00666234410967248,
 0.0,
 0.0027406888885284086,
 0.017039344202032902,
 0.028985732168099965,
 0.0011491141731021504,
 0.0,
 0.0008523827253787974,
 0.0,
 0.006399222121836079,
 0.04703025221877888,
 0.03830201506662445,
 0.020767713452616077,
 0.01662746423452499,
 0.015919680265923164,
 0.012917910410705558,
 0.005559985458040595,
 0.0,
 0.00812366089519645,
 0.02275875

In [50]:
segment_boundaries

[0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
